In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *

# Data Access

In [0]:
app_id = '18f0628e-d082-4ee4-83a1-21a3c22c4da7'
tenant_id = 'c3621375-72db-4931-8135-0fa380e9ba78'
secret_value = '******'

spark.conf.set("fs.azure.account.auth.type.fantasybookdatastorage.dfs.core.windows.net", "OAuth")
spark.conf.set("fs.azure.account.oauth.provider.type.fantasybookdatastorage.dfs.core.windows.net", "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider")
spark.conf.set("fs.azure.account.oauth2.client.id.fantasybookdatastorage.dfs.core.windows.net", app_id)
spark.conf.set("fs.azure.account.oauth2.client.secret.fantasybookdatastorage.dfs.core.windows.net", secret_value)
spark.conf.set(f"fs.azure.account.oauth2.client.endpoint.fantasybookdatastorage.dfs.core.windows.net", "https://login.microsoftonline.com/c3621375-72db-4931-8135-0fa380e9ba78/oauth2/token")

# Creating Dimension

## Create Flag Parameter

In [0]:
dbutils.widgets.text("incremental_flag", "0")

incremental_flag = dbutils.widgets.get("incremental_flag")
print(incremental_flag)

1


## Authors Dimension Table

### Select Relevant Columns

In [0]:
df_authors_src = spark.sql('''
                select authorKey, name, birth_date, death_date, lastModifiedDate
                from parquet.`abfss://silver@fantasybookdatastorage.dfs.core.windows.net/authors`
                ''')

df_authors_src.display()

authorKey name birth_date death_date lastModifiedDate OL2869173A Alex Holder null null 2008-04-29T15:03:11.581851Z OL1389492A Kathleen Olmstead null null 2008-09-07T15:16:38.427017Z OL3237537A Mary E. Pearson null null 2008-04-30T09:38:13.731961Z OL220579A Norma Fox Mazer 1931 null 2021-04-27T01:36:43.149269Z OL7360388A Nik Kerry null null 2016-11-17T19:56:19.563866Z OL200181A Max Velthuijs 1923 null 2008-09-06T22:29:13.235957Z OL1759717A Barbara Softly null null 2010-12-05T02:28:43.891306Z OL1221336A Wilfried Blecher null null 2008-08-18T22:48:36.960933Z OL15017001A Ud Din null null 2025-02-21T21:05:19.661035Z OL7524496A 朝霧カフカ 1984 March 17 null 2025-04-10T21:33:49.094528Z OL2630818A Sienna Mercer null null 2008-04-29T13:35:46.87638Z OL3816592A Donna Marie Robb null null 2008-04-30T20:50:18.033121Z OL7405642A Traci Chee null null 2024-03-13T07:40:03.647716Z OL844811A Sandra S. Kahn null null 2008-08-22T21:02:42.479525Z OL19989A Jan Wahl 1933 2019 2024-09-06T16:43:29.626577Z OL216446A Richard La Plante null null 2021-10-04T02:32:37.372391Z OL6611493A Laura Bingham null null 2009-05-15T00:50:33.564481Z OL226311A Ann Hood 1956 null 2011-04-21T03:19:16.477439Z OL2675866A Eoin Mcnamee null null 2008-04-29T13:35:46.87638Z OL226967A Mary Clark null null 2008-09-07T05:08:50.971393Z OL1549542A Stephen Goldin 28 February 1947 null 2023-05-24T16:34:55.544216Z OL1303448A Inoue, Makoto 1927 null 2008-04-01T03:28:50.625462Z OL74952A Joanne Findon 1957 null 2008-09-08T10:05:45.912836Z OL2811105A Carrie Jones 1971 null 2022-03-28T10:22:06.448672Z OL2038162A Jack Sendak null null 2008-08-20T23:23:47.898372Z OL776952A Dwight E. Crevelt null null 2008-08-24T10:22:35.906715Z OL949860A M. Coleman Easton null null 2008-08-21T23:50:40.445676Z OL1811443A Russ Leadabrand null null 2008-08-28T11:33:59.97453Z OL24533A John Bemelmans Marciano null null 2008-09-11T14:53:15.135202Z OL2101543A Ingrid Picker null null 2008-08-20T05:15:59.505057Z OL7292942A Francesca Haig null null 2016-09-07T06:32:10.431361Z OL6731969A YoYo. null null 2009-09-29T23:51:16.011582Z OL5172238A Stacey Jay null null 2008-09-26T21:41:40.246683Z OL7612231A Michelle Modesto null null 2019-07-19T19:31:15.015367Z OL6818792A J. R King null null 2010-07-01T02:10:48.376564Z OL8006740A R.A. Mejia null null 2020-07-17T17:46:51.654555Z OL3747118A Peter Devries null null 2008-04-30T20:50:18.033121Z OL3092246A Josepha Sherman 12 December 1946 23 August 2012 2023-06-18T08:29:04.351378Z OL31238A Katherine Kurtz 1944 null 2022-01-06T23:08:33.244404Z OL7524260A Hiroshi Saitō 1952 null 2019-05-23T22:53:18.58778Z OL6437370A Sarah Baylis 1956 1987 2008-11-11T10:18:10.681544Z OL7482384A Zack Loran Clark null null 2019-03-19T00:22:02.777626Z OL1917715A Richard Kleiner null null 2008-08-24T00:20:34.09917Z OL7409261A Daniel Laverdure null null 2018-02-27T05:09:02.955177Z OL1434382A Candace Havens 1963 null 2008-09-07T20:32:58.504826Z OL627874A Roger Hargreaves 9 May 1935 11 September 1988 2023-08-03T08:26:50.778661Z OL240049A Franny Billingsley 1954 null 2020-09-27T04:15:34.968338Z OL546221A Ken Ramirez null null 2008-08-29T19:34:12.315035Z OL9089471A D. T. Kizis null null 2021-01-23T15:30:25.189543Z OL10364781A Dark Blue Coconut Milk null null 2022-05-21T16:19:18.251825Z OL7511812A B. A. Williamson null null 2019-05-11T19:31:57.810571Z OL7302732A Kurt Hartman null null 2016-10-14T03:39:28.799318Z OL10341159A Justine Niogret null null 2022-03-21T14:27:04.175952Z OL360342A Wayne Anderson null null 2008-09-01T17:46:34.881939Z OL7434274A Audrey Coulthurst null null 2018-11-24T16:27:13.988193Z OL9005213A Taneka Stotts null null 2020-12-11T01:26:42.872033Z OL14089637A Nova Kane null null 2024-08-23T16:15:34.3467Z OL318496A Cherry Wilder null null 2008-09-04T19:37:40.861681Z OL6532050A Carrie Mac 1975 null 2008-12-21T04:30:32.612052Z OL3266150A Morgan Howell null null 2008-04-30T09:38:13.731961Z OL2812814A Martha Brockenbrough null null 2008-04-29T15:03:11.581851Z OL7012084A Hannah Dolan null null 2011-10-23T

### Authors Dimension Table Sink - Initial and Incremental Load

In [0]:
gold_authors_path = 'abfss://gold@fantasybookdatastorage.dfs.core.windows.net/authors'
gold_authors_path_files = dbutils.fs.ls(gold_authors_path)

if len(gold_authors_path_files) == 0:
    df_authors_sink = spark.sql('''
                        select distinct(authorKey) as authorKey, name, birth_date, death_date, lastModifiedDate, 1 as dimAuthorKey
                        from parquet.`abfss://silver@fantasybookdatastorage.dfs.core.windows.net/authors`
                        where 1=0 
                        ''')
else:
    df_authors_sink = spark.sql('''
                        select distinct(authorKey) as authorKey, name, birth_date, death_date, lastModifiedDate, dimAuthorKey
                        from delta.`abfss://gold@fantasybookdatastorage.dfs.core.windows.net/authors`
                        ''')
    
df_authors_sink.display()

authorKey name birth_date death_date lastModifiedDate dimAuthorKey

### Filtering between existing and new records

In [0]:
df_authors_filter = df_authors_src\
                    .join(df_authors_sink, df_authors_src["authorKey"] == df_authors_sink["authorKey"], 'left')\
                    .select(df_authors_src["authorKey"], df_authors_src["name"], df_authors_src["birth_date"], df_authors_src["death_date"], df_authors_src["lastModifiedDate"], df_authors_sink["dimAuthorKey"])

df_authors_filter_existing = df_authors_filter.filter(col("dimAuthorKey").isNotNull())
df_authors_filter_new = df_authors_filter.filter(col("dimAuthorKey").isNull())\
                        .select(df_authors_filter["authorKey"], df_authors_filter["name"], df_authors_filter["birth_date"], df_authors_filter["death_date"], df_authors_filter["lastModifiedDate"])

df_authors_filter_new.display()

authorKey name birth_date death_date lastModifiedDate OL2869173A Alex Holder null null 2008-04-29T15:03:11.581851Z OL1389492A Kathleen Olmstead null null 2008-09-07T15:16:38.427017Z OL3237537A Mary E. Pearson null null 2008-04-30T09:38:13.731961Z OL220579A Norma Fox Mazer 1931 null 2021-04-27T01:36:43.149269Z OL7360388A Nik Kerry null null 2016-11-17T19:56:19.563866Z OL200181A Max Velthuijs 1923 null 2008-09-06T22:29:13.235957Z OL1759717A Barbara Softly null null 2010-12-05T02:28:43.891306Z OL1221336A Wilfried Blecher null null 2008-08-18T22:48:36.960933Z OL15017001A Ud Din null null 2025-02-21T21:05:19.661035Z OL7524496A 朝霧カフカ 1984 March 17 null 2025-04-10T21:33:49.094528Z OL2630818A Sienna Mercer null null 2008-04-29T13:35:46.87638Z OL3816592A Donna Marie Robb null null 2008-04-30T20:50:18.033121Z OL7405642A Traci Chee null null 2024-03-13T07:40:03.647716Z OL844811A Sandra S. Kahn null null 2008-08-22T21:02:42.479525Z OL19989A Jan Wahl 1933 2019 2024-09-06T16:43:29.626577Z OL216446A Richard La Plante null null 2021-10-04T02:32:37.372391Z OL6611493A Laura Bingham null null 2009-05-15T00:50:33.564481Z OL226311A Ann Hood 1956 null 2011-04-21T03:19:16.477439Z OL2675866A Eoin Mcnamee null null 2008-04-29T13:35:46.87638Z OL226967A Mary Clark null null 2008-09-07T05:08:50.971393Z OL1549542A Stephen Goldin 28 February 1947 null 2023-05-24T16:34:55.544216Z OL1303448A Inoue, Makoto 1927 null 2008-04-01T03:28:50.625462Z OL74952A Joanne Findon 1957 null 2008-09-08T10:05:45.912836Z OL2811105A Carrie Jones 1971 null 2022-03-28T10:22:06.448672Z OL2038162A Jack Sendak null null 2008-08-20T23:23:47.898372Z OL776952A Dwight E. Crevelt null null 2008-08-24T10:22:35.906715Z OL949860A M. Coleman Easton null null 2008-08-21T23:50:40.445676Z OL1811443A Russ Leadabrand null null 2008-08-28T11:33:59.97453Z OL24533A John Bemelmans Marciano null null 2008-09-11T14:53:15.135202Z OL2101543A Ingrid Picker null null 2008-08-20T05:15:59.505057Z OL7292942A Francesca Haig null null 2016-09-07T06:32:10.431361Z OL6731969A YoYo. null null 2009-09-29T23:51:16.011582Z OL5172238A Stacey Jay null null 2008-09-26T21:41:40.246683Z OL7612231A Michelle Modesto null null 2019-07-19T19:31:15.015367Z OL6818792A J. R King null null 2010-07-01T02:10:48.376564Z OL8006740A R.A. Mejia null null 2020-07-17T17:46:51.654555Z OL3747118A Peter Devries null null 2008-04-30T20:50:18.033121Z OL3092246A Josepha Sherman 12 December 1946 23 August 2012 2023-06-18T08:29:04.351378Z OL31238A Katherine Kurtz 1944 null 2022-01-06T23:08:33.244404Z OL7524260A Hiroshi Saitō 1952 null 2019-05-23T22:53:18.58778Z OL6437370A Sarah Baylis 1956 1987 2008-11-11T10:18:10.681544Z OL7482384A Zack Loran Clark null null 2019-03-19T00:22:02.777626Z OL1917715A Richard Kleiner null null 2008-08-24T00:20:34.09917Z OL7409261A Daniel Laverdure null null 2018-02-27T05:09:02.955177Z OL1434382A Candace Havens 1963 null 2008-09-07T20:32:58.504826Z OL627874A Roger Hargreaves 9 May 1935 11 September 1988 2023-08-03T08:26:50.778661Z OL240049A Franny Billingsley 1954 null 2020-09-27T04:15:34.968338Z OL546221A Ken Ramirez null null 2008-08-29T19:34:12.315035Z OL9089471A D. T. Kizis null null 2021-01-23T15:30:25.189543Z OL10364781A Dark Blue Coconut Milk null null 2022-05-21T16:19:18.251825Z OL7511812A B. A. Williamson null null 2019-05-11T19:31:57.810571Z OL7302732A Kurt Hartman null null 2016-10-14T03:39:28.799318Z OL10341159A Justine Niogret null null 2022-03-21T14:27:04.175952Z OL360342A Wayne Anderson null null 2008-09-01T17:46:34.881939Z OL7434274A Audrey Coulthurst null null 2018-11-24T16:27:13.988193Z OL9005213A Taneka Stotts null null 2020-12-11T01:26:42.872033Z OL14089637A Nova Kane null null 2024-08-23T16:15:34.3467Z OL318496A Cherry Wilder null null 2008-09-04T19:37:40.861681Z OL6532050A Carrie Mac 1975 null 2008-12-21T04:30:32.612052Z OL3266150A Morgan Howell null null 2008-04-30T09:38:13.731961Z OL2812814A Martha Brockenbrough null null 2008-04-29T15:03:11.581851Z OL7012084A Hannah Dolan null null 2011-10-23T

### Create Surrogate/Dimension Key

In [0]:
if incremental_flag == '0':
    max_dim_key_value = 0
else:
    max_dim_key_value_df = spark.sql("select max(dimAuthorKey) from delta.`abfss://gold@fantasybookdatastorage.dfs.core.windows.net/authors`")
    max_dim_key_value = max_dim_key_value_df.collect()[0][0]

df_authors_filter_new = df_authors_filter_new.withColumn("dimAuthorKey", lit(max_dim_key_value + monotonically_increasing_id() + 1))
df_authors_filter_new.display()

authorKey name birth_date death_date lastModifiedDate dimAuthorKey OL2869173A Alex Holder null null 2008-04-29T15:03:11.581851Z 1 OL1389492A Kathleen Olmstead null null 2008-09-07T15:16:38.427017Z 2 OL3237537A Mary E. Pearson null null 2008-04-30T09:38:13.731961Z 3 OL220579A Norma Fox Mazer 1931 null 2021-04-27T01:36:43.149269Z 4 OL7360388A Nik Kerry null null 2016-11-17T19:56:19.563866Z 5 OL200181A Max Velthuijs 1923 null 2008-09-06T22:29:13.235957Z 6 OL1759717A Barbara Softly null null 2010-12-05T02:28:43.891306Z 7 OL1221336A Wilfried Blecher null null 2008-08-18T22:48:36.960933Z 8 OL15017001A Ud Din null null 2025-02-21T21:05:19.661035Z 9 OL7524496A 朝霧カフカ 1984 March 17 null 2025-04-10T21:33:49.094528Z 10 OL2630818A Sienna Mercer null null 2008-04-29T13:35:46.87638Z 11 OL3816592A Donna Marie Robb null null 2008-04-30T20:50:18.033121Z 12 OL7405642A Traci Chee null null 2024-03-13T07:40:03.647716Z 13 OL844811A Sandra S. Kahn null null 2008-08-22T21:02:42.479525Z 14 OL19989A Jan Wahl 1933 2019 2024-09-06T16:43:29.626577Z 15 OL216446A Richard La Plante null null 2021-10-04T02:32:37.372391Z 16 OL6611493A Laura Bingham null null 2009-05-15T00:50:33.564481Z 17 OL226311A Ann Hood 1956 null 2011-04-21T03:19:16.477439Z 18 OL2675866A Eoin Mcnamee null null 2008-04-29T13:35:46.87638Z 19 OL226967A Mary Clark null null 2008-09-07T05:08:50.971393Z 20 OL1549542A Stephen Goldin 28 February 1947 null 2023-05-24T16:34:55.544216Z 21 OL1303448A Inoue, Makoto 1927 null 2008-04-01T03:28:50.625462Z 22 OL74952A Joanne Findon 1957 null 2008-09-08T10:05:45.912836Z 23 OL2811105A Carrie Jones 1971 null 2022-03-28T10:22:06.448672Z 24 OL2038162A Jack Sendak null null 2008-08-20T23:23:47.898372Z 25 OL776952A Dwight E. Crevelt null null 2008-08-24T10:22:35.906715Z 26 OL949860A M. Coleman Easton null null 2008-08-21T23:50:40.445676Z 27 OL1811443A Russ Leadabrand null null 2008-08-28T11:33:59.97453Z 28 OL24533A John Bemelmans Marciano null null 2008-09-11T14:53:15.135202Z 29 OL2101543A Ingrid Picker null null 2008-08-20T05:15:59.505057Z 30 OL7292942A Francesca Haig null null 2016-09-07T06:32:10.431361Z 31 OL6731969A YoYo. null null 2009-09-29T23:51:16.011582Z 32 OL5172238A Stacey Jay null null 2008-09-26T21:41:40.246683Z 33 OL7612231A Michelle Modesto null null 2019-07-19T19:31:15.015367Z 34 OL6818792A J. R King null null 2010-07-01T02:10:48.376564Z 35 OL8006740A R.A. Mejia null null 2020-07-17T17:46:51.654555Z 36 OL3747118A Peter Devries null null 2008-04-30T20:50:18.033121Z 37 OL3092246A Josepha Sherman 12 December 1946 23 August 2012 2023-06-18T08:29:04.351378Z 38 OL31238A Katherine Kurtz 1944 null 2022-01-06T23:08:33.244404Z 39 OL7524260A Hiroshi Saitō 1952 null 2019-05-23T22:53:18.58778Z 40 OL6437370A Sarah Baylis 1956 1987 2008-11-11T10:18:10.681544Z 41 OL7482384A Zack Loran Clark null null 2019-03-19T00:22:02.777626Z 42 OL1917715A Richard Kleiner null null 2008-08-24T00:20:34.09917Z 43 OL7409261A Daniel Laverdure null null 2018-02-27T05:09:02.955177Z 44 OL1434382A Candace Havens 1963 null 2008-09-07T20:32:58.504826Z 45 OL627874A Roger Hargreaves 9 May 1935 11 September 1988 2023-08-03T08:26:50.778661Z 46 OL240049A Franny Billingsley 1954 null 2020-09-27T04:15:34.968338Z 47 OL546221A Ken Ramirez null null 2008-08-29T19:34:12.315035Z 48 OL9089471A D. T. Kizis null null 2021-01-23T15:30:25.189543Z 49 OL10364781A Dark Blue Coconut Milk null null 2022-05-21T16:19:18.251825Z 50 OL7511812A B. A. Williamson null null 2019-05-11T19:31:57.810571Z 51 OL7302732A Kurt Hartman null null 2016-10-14T03:39:28.799318Z 52 OL10341159A Justine Niogret null null 2022-03-21T14:27:04.175952Z 53 OL360342A Wayne Anderson null null 2008-09-01T17:46:34.881939Z 54 OL7434274A Audrey Coulthurst null null 2018-11-24T16:27:13.988193Z 55 OL9005213A Taneka Stotts null null 2020-12-11T01:26:42.872033Z 56 OL14089637A Nova Kane null null 2024-08-23T16:15:34.3467Z 57 OL318496A Cherry Wilder null null 2008-09-04T19:37:40.861681Z 58 OL6532050A Carrie Mac 1975 null 2008-12-21T04:30:32.612052Z 

### Create New Final Authors Dimension Table

In [0]:
df_authors_final = df_authors_filter_existing.union(df_authors_filter_new)
df_authors_final.display()

authorKey name birth_date death_date lastModifiedDate dimAuthorKey OL2869173A Alex Holder null null 2008-04-29T15:03:11.581851Z 1 OL1389492A Kathleen Olmstead null null 2008-09-07T15:16:38.427017Z 2 OL3237537A Mary E. Pearson null null 2008-04-30T09:38:13.731961Z 3 OL220579A Norma Fox Mazer 1931 null 2021-04-27T01:36:43.149269Z 4 OL7360388A Nik Kerry null null 2016-11-17T19:56:19.563866Z 5 OL200181A Max Velthuijs 1923 null 2008-09-06T22:29:13.235957Z 6 OL1759717A Barbara Softly null null 2010-12-05T02:28:43.891306Z 7 OL1221336A Wilfried Blecher null null 2008-08-18T22:48:36.960933Z 8 OL15017001A Ud Din null null 2025-02-21T21:05:19.661035Z 9 OL7524496A 朝霧カフカ 1984 March 17 null 2025-04-10T21:33:49.094528Z 10 OL2630818A Sienna Mercer null null 2008-04-29T13:35:46.87638Z 11 OL3816592A Donna Marie Robb null null 2008-04-30T20:50:18.033121Z 12 OL7405642A Traci Chee null null 2024-03-13T07:40:03.647716Z 13 OL844811A Sandra S. Kahn null null 2008-08-22T21:02:42.479525Z 14 OL19989A Jan Wahl 1933 2019 2024-09-06T16:43:29.626577Z 15 OL216446A Richard La Plante null null 2021-10-04T02:32:37.372391Z 16 OL6611493A Laura Bingham null null 2009-05-15T00:50:33.564481Z 17 OL226311A Ann Hood 1956 null 2011-04-21T03:19:16.477439Z 18 OL2675866A Eoin Mcnamee null null 2008-04-29T13:35:46.87638Z 19 OL226967A Mary Clark null null 2008-09-07T05:08:50.971393Z 20 OL1549542A Stephen Goldin 28 February 1947 null 2023-05-24T16:34:55.544216Z 21 OL1303448A Inoue, Makoto 1927 null 2008-04-01T03:28:50.625462Z 22 OL74952A Joanne Findon 1957 null 2008-09-08T10:05:45.912836Z 23 OL2811105A Carrie Jones 1971 null 2022-03-28T10:22:06.448672Z 24 OL2038162A Jack Sendak null null 2008-08-20T23:23:47.898372Z 25 OL776952A Dwight E. Crevelt null null 2008-08-24T10:22:35.906715Z 26 OL949860A M. Coleman Easton null null 2008-08-21T23:50:40.445676Z 27 OL1811443A Russ Leadabrand null null 2008-08-28T11:33:59.97453Z 28 OL24533A John Bemelmans Marciano null null 2008-09-11T14:53:15.135202Z 29 OL2101543A Ingrid Picker null null 2008-08-20T05:15:59.505057Z 30 OL7292942A Francesca Haig null null 2016-09-07T06:32:10.431361Z 31 OL6731969A YoYo. null null 2009-09-29T23:51:16.011582Z 32 OL5172238A Stacey Jay null null 2008-09-26T21:41:40.246683Z 33 OL7612231A Michelle Modesto null null 2019-07-19T19:31:15.015367Z 34 OL6818792A J. R King null null 2010-07-01T02:10:48.376564Z 35 OL8006740A R.A. Mejia null null 2020-07-17T17:46:51.654555Z 36 OL3747118A Peter Devries null null 2008-04-30T20:50:18.033121Z 37 OL3092246A Josepha Sherman 12 December 1946 23 August 2012 2023-06-18T08:29:04.351378Z 38 OL31238A Katherine Kurtz 1944 null 2022-01-06T23:08:33.244404Z 39 OL7524260A Hiroshi Saitō 1952 null 2019-05-23T22:53:18.58778Z 40 OL6437370A Sarah Baylis 1956 1987 2008-11-11T10:18:10.681544Z 41 OL7482384A Zack Loran Clark null null 2019-03-19T00:22:02.777626Z 42 OL1917715A Richard Kleiner null null 2008-08-24T00:20:34.09917Z 43 OL7409261A Daniel Laverdure null null 2018-02-27T05:09:02.955177Z 44 OL1434382A Candace Havens 1963 null 2008-09-07T20:32:58.504826Z 45 OL627874A Roger Hargreaves 9 May 1935 11 September 1988 2023-08-03T08:26:50.778661Z 46 OL240049A Franny Billingsley 1954 null 2020-09-27T04:15:34.968338Z 47 OL546221A Ken Ramirez null null 2008-08-29T19:34:12.315035Z 48 OL9089471A D. T. Kizis null null 2021-01-23T15:30:25.189543Z 49 OL10364781A Dark Blue Coconut Milk null null 2022-05-21T16:19:18.251825Z 50 OL7511812A B. A. Williamson null null 2019-05-11T19:31:57.810571Z 51 OL7302732A Kurt Hartman null null 2016-10-14T03:39:28.799318Z 52 OL10341159A Justine Niogret null null 2022-03-21T14:27:04.175952Z 53 OL360342A Wayne Anderson null null 2008-09-01T17:46:34.881939Z 54 OL7434274A Audrey Coulthurst null null 2018-11-24T16:27:13.988193Z 55 OL9005213A Taneka Stotts null null 2020-12-11T01:26:42.872033Z 56 OL14089637A Nova Kane null null 2024-08-23T16:15:34.3467Z 57 OL318496A Cherry Wilder null null 2008-09-04T19:37:40.861681Z 58 OL6532050A Carrie Mac 1975 null 2008-12-21T04:30:32.612052Z 

# Creating SCD Type 1 (Upsert)

In [0]:
from delta.tables import DeltaTable


## Authors Dimension Table

In [0]:
# Initial Run
if len(gold_authors_path_files) == 0:
    df_authors_final.write.format("delta")\
                .mode("overwrite")\
                .option("path", gold_authors_path)\
                .saveAsTable("authorsDimTable")

# Incremental Run
else:
    authorsDim_deltatable = DeltaTable.forPath(spark, gold_authors_path)
    authorsDim_deltatable.alias("authorsDimTable")\
                    .merge(df_authors_final.alias("updates"), "authorsDimTable.dimAuthorKey = updates.dimAuthorKey")\
                    .whenMatchedUpdateAll()\
                    .whenNotMatchedInsertAll()\
                    .execute()